In [1]:
import pandas as pd
import numpy as np
from src import data_cleaning as dc
from collections import defaultdict
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt

In [2]:
people_df = pd.read_csv('src/data/baseballdatabank-master/core/People.csv')
batting_df = pd.read_csv('src/data/baseballdatabank-master/core/Batting.csv')
fielding_df = pd.read_csv('src/data/baseballdatabank-master/core/Fielding.csv')

In [3]:
# initial drop
batting_df2 = dc.initial_drop(batting_df)
batting_df2.head()

playerID  yearID   G   AB   R   H  2B  3B  HR   RBI   SB   CS  BB   SO  \
0  abercda01    1871   1    4   0   0   0   0   0   0.0  0.0  0.0   0  0.0   
1   addybo01    1871  25  118  30  32   6   0   0  13.0  8.0  1.0   4  0.0   
2  allisar01    1871  29  137  28  40   4   5   0  19.0  3.0  1.0   2  5.0   
3  allisdo01    1871  27  133  28  44  10   2   2  27.0  1.0  1.0   0  2.0   
4  ansonca01    1871  25  120  29  39  11   3   0  16.0  6.0  2.0   2  1.0   

   IBB  HBP  SH  SF  GIDP  
0  NaN  NaN NaN NaN   0.0  
1  NaN  NaN NaN NaN   0.0  
2  NaN  NaN NaN NaN   1.0  
3  NaN  NaN NaN NaN   0.0  
4  NaN  NaN NaN NaN   0.0

In [4]:
# combine stints into single year collection
batting_df3 = dc.combine_stints(batting_df2)
batting_df3.head()

Combining multiple stints into single years...


playerID  yearID   G  AB  R  H  2B  3B  HR  RBI   SB   CS  BB   SO  IBB  \
0  aardsda01    2004  11   0  0  0   0   0   0  0.0  0.0  0.0   0  0.0  0.0   
1  aardsda01    2006  45   2  0  0   0   0   0  0.0  0.0  0.0   0  0.0  0.0   
2  aardsda01    2007  25   0  0  0   0   0   0  0.0  0.0  0.0   0  0.0  0.0   
3  aardsda01    2008  47   1  0  0   0   0   0  0.0  0.0  0.0   0  1.0  0.0   
4  aardsda01    2009  73   0  0  0   0   0   0  0.0  0.0  0.0   0  0.0  0.0   

   HBP   SH   SF  GIDP  
0  0.0  0.0  0.0   0.0  
1  0.0  1.0  0.0   0.0  
2  0.0  0.0  0.0   0.0  
3  0.0  0.0  0.0   0.0  
4  0.0  0.0  0.0   0.0

In [5]:
# map each player's most common position to their batting stats
bat_with_pos_df = dc.map_position(batting_df3, fielding_df)
bat_with_pos_df.head()

Mapping positions to batting stats...


playerID  yearID    G   AB    R    H  2B  3B  HR    RBI   SB   CS  BB  \
9   aaronha01    1954  122  468   58  131  27   6  13   69.0  2.0  2.0  28   
10  aaronha01    1955  153  602  105  189  37   9  27  106.0  3.0  1.0  49   
11  aaronha01    1956  153  609  106  200  34  14  26   92.0  2.0  4.0  37   
12  aaronha01    1957  151  615  118  198  27   6  44  132.0  1.0  1.0  57   
13  aaronha01    1958  153  601  109  196  34   4  30   95.0  4.0  1.0  59   

      SO   IBB  HBP   SH   SF  GIDP pos  
9   39.0   0.0  3.0  6.0  4.0  13.0  OF  
10  61.0   5.0  3.0  7.0  4.0  20.0  OF  
11  54.0   6.0  2.0  5.0  7.0  21.0  OF  
12  58.0  15.0  0.0  0.0  3.0  13.0  OF  
13  49.0  16.0  1.0  0.0  3.0  21.0  OF

In [6]:
bat_with_pos_df['avg'] = bat_with_pos_df['H'] / bat_with_pos_df['AB']

In [7]:
# def condense_df(df0):
#     df = df0.set_index('playerID')
#     player_list = []
#     for player in df.index.unique():
#         def_dict = defaultdict(str)
#         def_dict['playerID'] = player   
#         if isinstance(df.loc[player, 'pos'], str):
#             def_dict['pos'] = df.loc[player, 'pos']
#         else:
#             def_dict['pos'] = df.loc[player, 'pos'].unique()[0]
            
#         for col in df.columns:
#             if col == 'yearID' or col == 'pos':
#                 continue
#             try:
#                 for i, v in enumerate(df.loc[player, col]):
#                     if i > 6:
#                         continue
#                     key = 'year' + str(i + 1) + '_' + col
#                     def_dict[key] = v
#             except:
#                 continue # skip players with only 1 year of data
#         player_list.append(def_dict)
#     new_df = pd.DataFrame(player_list)
#     return new_df.dropna() #drop players without 7 years of data

In [8]:
test_df = dc.condense_df(bat_with_pos_df)

In [9]:
avg_pos_cols = [col for col in test_df.columns if 'avg' in col or 'pos' in col]
avg_cols = [col for col in test_df.columns if 'avg' in col]
avg_pos_cols

['year1_avg',
 'year2_avg',
 'year3_avg',
 'year4_avg',
 'year5_avg',
 'year6_avg',
 'year7_avg',
 'pos_1B',
 'pos_2B',
 'pos_3B',
 'pos_C',
 'pos_OF',
 'pos_SS']

In [10]:
test_df_avgs_pos = test_df[avg_pos_cols]
test_df_avgs = test_df[avg_cols]

In [11]:
X_pos = test_df_avgs_pos
y_pos = X_pos.pop('year7_avg')

X_train_pos, X_test_pos, y_train_pos, y_true_pos = train_test_split(X_pos, y_pos)

regr = RandomForestRegressor()
regr.fit(X_train_pos, y_train_pos)
y_pred_pos = regr.predict(X_test_pos)

In [12]:
results_pos = pd.DataFrame(data=y_true_pos)
results_pos['predicted'] = y_pred_pos
results_pos['diff'] = results_pos['year7_avg'] - results_pos['predicted']
results_pos.reset_index(drop=True, inplace=True)
results_pos

year7_avg  predicted      diff
0     0.163636   0.257794 -0.094158
1     0.255906   0.255319  0.000587
2     0.287671   0.232100  0.055571
3     0.276423   0.267575  0.008848
4     0.278788   0.263081  0.015707
5     0.218391   0.266502 -0.048111
6     0.294643   0.218324  0.076319
7     0.258427   0.235332  0.023095
8     0.297800   0.271127  0.026673
9     0.250996   0.298522 -0.047526
10    0.232323   0.210035  0.022288
11    0.342105   0.251557  0.090548
12    0.259398   0.237351  0.022048
13    0.335570   0.315528  0.020043
14    0.264501   0.215590  0.048911
15    0.279503   0.252047  0.027457
16    0.225882   0.085586  0.140296
17    0.235669   0.254087 -0.018418
18    0.281250   0.238007  0.043243
19    0.278075   0.251104  0.026971
20    0.228916   0.274769 -0.045853
21    0.227273   0.274101 -0.046828
22    0.259582   0.259090  0.000492
23    0.239726   0.343975 -0.104249
24    0.160714   0.247194 -0.086480
25    0.133333   0.259636 -0.126303
26    0.160920   0.229648 -0.068728
27    0.276404   0.262486  0.013919
28    0.282895   0.269229  0.013665
29    0.267327   0.227879  0.039447
..         ...        ...       ...
785   0.228412   0.255372 -0.026959
786   0.270833   0.242891  0.027942
787   0.250000   0.327050 -0.077050
788   0.361702   0.240480  0.121222
789   0.277108   0.194141  0.082967
790   0.250000   0.220885  0.029115
791   0.294118   0.286110  0.008008
792   0.177215   0.229240 -0.052025
793   0.280083   0.314602 -0.034519
794   0.277409   0.260311  0.017097
795   0.200000   0.220566 -0.020566
796   0.260586   0.248572  0.012015
797   0.244186   0.275357 -0.031171
798   0.268293   0.291198 -0.022905
799   0.205128   0.269746 -0.064618
800   0.234940   0.262045 -0.027106
801   0.353135   0.267496  0.085640
802   0.297391   0.259803  0.037588
803   0.224719   0.271651 -0.046932
804   0.281915   0.264829  0.017086
805   0.289474   0.256870  0.032604
806   0.256637   0.232260  0.024377
807   0.266476   0.190081  0.076394
808   0.235514   0.266965 -0.031451
809   0.278195   0.281192 -0.002996
810   0.220957   0.245518 -0.024562
811   0.273684   0.218321  0.055363
812   0.204082   0.235683 -0.031601
813   0.218978   0.215592  0.003386
814   0.234192   0.236658 -0.002466

[815 rows x 3 columns]

In [13]:
mse_pos = mean_squared_error(y_true_pos, y_pred_pos)
rmse_pos = mse_pos**0.5
score_pos = regr.score(X_test_pos, y_true_pos)
print('MSE: {:.3f}\n'\
      'RMSE: {:.3f}\n'\
      'Score: {:.3f}'.format(mse_pos, rmse_pos, score_pos))

MSE: 0.005
RMSE: 0.067
Score: 0.003


In [14]:
X_avg = test_df_avgs
y_avg = X_avg.pop('year7_avg')

X_train_avg, X_test_avg, y_train_avg, y_true_avg = train_test_split(X_avg, y_avg)
regr_avg = RandomForestRegressor()
regr_avg.fit(X_train_avg, y_train_avg)
y_pred_avg = regr_avg.predict(X_test_avg)

In [15]:
results_avg = pd.DataFrame(data=y_true_avg)
results_avg['predicted'] = y_pred_avg
results_avg['difference'] = results_avg['year7_avg'] - results_avg['predicted']
results_avg.reset_index(drop=True, inplace=True)
results_avg

year7_avg  predicted  difference
0     0.285942   0.263088    0.022854
1     0.271605   0.222128    0.049477
2     0.273171   0.238135    0.035035
3     0.282110   0.208352    0.073758
4     0.202899   0.320234   -0.117336
5     0.240942   0.270080   -0.029138
6     0.217039   0.265054   -0.048015
7     0.251603   0.270871   -0.019268
8     0.257143   0.264283   -0.007140
9     0.242718   0.274739   -0.032020
10    0.263780   0.266649   -0.002870
11    0.331407   0.283311    0.048096
12    0.209302   0.240300   -0.030998
13    0.333333   0.162163    0.171170
14    0.307203   0.256018    0.051186
15    0.234982   0.283245   -0.048263
16    0.248337   0.225546    0.022791
17    0.275132   0.258696    0.016437
18    0.409556   0.352399    0.057157
19    0.194915   0.226598   -0.031683
20    0.313596   0.292776    0.020821
21    0.288851   0.269559    0.019292
22    0.232394   0.236242   -0.003848
23    0.200000   0.226537   -0.026537
24    0.289238   0.238627    0.050611
25    0.223176   0.263391   -0.040215
26    0.343696   0.310739    0.032957
27    0.202381   0.197621    0.004760
28    0.262582   0.217319    0.045263
29    0.240506   0.253048   -0.012541
..         ...        ...         ...
785   0.315603   0.210299    0.105303
786   0.206349   0.265586   -0.059237
787   0.166667   0.119474    0.047192
788   0.336052   0.266365    0.069687
789   0.238095   0.243084   -0.004988
790   0.250000   0.254420   -0.004420
791   0.211268   0.252405   -0.041137
792   0.255319   0.229239    0.026081
793   0.250000   0.251065   -0.001065
794   0.215278   0.236298   -0.021020
795   0.271186   0.252442    0.018744
796   0.198529   0.245375   -0.046846
797   0.291822   0.288146    0.003675
798   0.234234   0.281463   -0.047229
799   0.286624   0.228071    0.058553
800   0.259442   0.267256   -0.007814
801   0.269972   0.246697    0.023275
802   0.257576   0.244420    0.013156
803   0.268022   0.297763   -0.029741
804   0.283451   0.264398    0.019053
805   0.250000   0.258625   -0.008625
806   0.254448   0.264991   -0.010542
807   0.272569   0.234554    0.038016
808   0.250000   0.274910   -0.024910
809   0.220126   0.236808   -0.016682
810   0.264822   0.277661   -0.012839
811   0.264368   0.268432   -0.004064
812   0.319073   0.307682    0.011391
813   0.275109   0.239656    0.035453
814   0.279070   0.248430    0.030640

[815 rows x 3 columns]

In [16]:
mse_avg = mean_squared_error(y_true_avg, y_pred_avg)
rmse_avg = mse_avg**0.5
score_avg = regr_avg.score(X_test_avg, y_true_avg)
print('MSE: {:.3f}\n'\
      'RMSE: {:.3f}\n'\
      'Score: {:.3f}'.format(mse_avg, rmse_avg, score_avg))

MSE: 0.003
RMSE: 0.059
Score: 0.049


In [17]:
results_pos.sort_values('diff')

year7_avg  predicted      diff
359   0.000000   0.288316 -0.288316
350   0.000000   0.240473 -0.240473
184   0.000000   0.239094 -0.239094
179   0.000000   0.235935 -0.235935
230   0.000000   0.228363 -0.228363
383   0.000000   0.223064 -0.223064
460   0.066667   0.276154 -0.209487
446   0.076923   0.242845 -0.165921
296   0.095238   0.261157 -0.165919
679   0.090909   0.251524 -0.160615
79    0.153846   0.305126 -0.151280
243   0.111111   0.260618 -0.149506
89    0.105263   0.252307 -0.147044
662   0.125000   0.265929 -0.140929
227   0.094118   0.233569 -0.139451
391   0.125000   0.260886 -0.135886
261   0.115385   0.251050 -0.135666
150   0.120000   0.254497 -0.134497
653   0.126984   0.260775 -0.133791
25    0.133333   0.259636 -0.126303
481   0.189873   0.309062 -0.119189
494   0.129032   0.247092 -0.118060
765   0.133333   0.251259 -0.117926
642   0.108696   0.225826 -0.117130
432   0.133333   0.245928 -0.112595
613   0.161491   0.273989 -0.112498
163   0.174757   0.282779 -0.108021
626   0.090909   0.198714 -0.107805
246   0.137255   0.244596 -0.107341
706   0.152174   0.258334 -0.106160
..         ...        ...       ...
127   0.313725   0.225490  0.088236
162   0.285714   0.197230  0.088484
684   0.333333   0.243646  0.089687
11    0.342105   0.251557  0.090548
307   0.372323   0.279604  0.092718
702   0.330275   0.236964  0.093311
436   0.215596   0.119387  0.096210
90    0.252336   0.155182  0.097155
514   0.372093   0.273647  0.098446
175   0.312500   0.213960  0.098540
484   0.345930   0.247272  0.098658
736   0.341912   0.240721  0.101190
458   0.302174   0.200297  0.101877
462   0.335541   0.232273  0.103268
301   0.396959   0.291792  0.105168
730   0.404858   0.298237  0.106621
77    0.265625   0.156951  0.108674
646   0.367521   0.253878  0.113643
625   0.393688   0.278085  0.115603
788   0.361702   0.240480  0.121222
336   0.350000   0.222512  0.127488
63    0.347826   0.216973  0.130853
16    0.225882   0.085586  0.140296
674   0.333333   0.158688  0.174645
598   0.500000   0.254744  0.245256
483   0.500000   0.239338  0.260662
781   0.333333   0.053222  0.280111
552   0.666667   0.206411  0.460256
593   1.000000   0.247006  0.752994
591   1.000000   0.200995  0.799005

[815 rows x 3 columns]

In [18]:
def trim_batters(df):
    # remove those seasons where batter had less than 100 ABs
    bat_with_pos_df = bat_with_pos_df[bat_with_pos_df['AB'] > 100]

    # remove batters with less than 7 years experience
    s = bat_with_pos_df['playerID'].value_counts()
    bat_with_pos_df = bat_with_pos_df[bat_with_pos_df['playerID'].isin(s[s > 6].index)]

    # select first 7 seasons
    bat_with_pos_df = bat_with_pos_df.groupby('playerID').head(7)

In [19]:
new_df = dc.trim_batters(bat_with_pos_df)

In [20]:
# this gets nth row (year) of a player and converts to dict
bat_with_pos_df.groupby('playerID').nth(6).T.to_dict('index')

{'2B': {'aaronha01': 20,
  'aaronto01': 2,
  'abbated01': 16,
  'abbotku01': 17,
  'abramca01': 12,
  'abreubo01': 50,
  'adairje01': 20,
  'adamsbe01': 4,
  'adamsbo03': 25,
  'adamsgl01': 10,
  'adamssp01': 14,
  'adcocjo01': 23,
  'ageeto01': 12,
  'agnewsa01': 7,
  'aguaylu01': 6,
  'aikenwi01': 7,
  'ainsmed01': 4,
  'aldremi01': 13,
  'alexaga01': 4,
  'alexama01': 0,
  'alexama02': 11,
  'alfoned01': 22,
  'alicelu01': 26,
  'allanan01': 1,
  'allenbe01': 12,
  'allenbo01': 1,
  'allench01': 1,
  'allendi01': 23,
  'allenet01': 6,
  'allenga01': 1,
  'allenha02': 2,
  'alleyge01': 3,
  'allisbo01': 27,
  'allisdo01': 2,
  'almadme01': 6,
  'almonbi01': 4,
  'alomaro01': 25,
  'alomasa01': 18,
  'alomasa02': 15,
  'alonsyo01': 34,
  'aloufe01': 26,
  'alouje01': 19,
  'alouma01': 18,
  'aloumo01': 29,
  'altmage01': 7,
  'altuvjo01': 39,
  'alvarlu01': 4,
  'alvarpe01': 20,
  'alvisma01': 17,
  'amalfjo01': 19,
  'amarari01': 5,
  'amarial01': 10,
  'amaroru01': 7,
  'amaroru02':

In [21]:
bat_with_pos_df.groupby('playerID').head(2)

playerID  yearID    G   AB    R    H  2B  3B  HR    RBI    ...     \
9      aaronha01    1954  122  468   58  131  27   6  13   69.0    ...      
10     aaronha01    1955  153  602  105  189  37   9  27  106.0    ...      
32     aaronto01    1962  141  334   54   77  20   2   8   38.0    ...      
33     aaronto01    1963   72  135    6   27   6   1   1   15.0    ...      
52      abadan01    2001    1    1    0    0   0   0   0    0.0    ...      
53      abadan01    2003    9   17    1    2   0   0   0    0.0    ...      
63     abadijo01    1875   12   49    4   11   0   0   0    5.0    ...      
64     abbated01    1897    3   10    0    3   0   0   0    0.0    ...      
65     abbated01    1898   25   92    9   21   4   0   0   14.0    ...      
78     abbeych01    1893   31  116   11   30   1   4   0   12.0    ...      
79     abbeych01    1894  129  523   95  164  26  18   7  101.0    ...      
84     abbotfr01    1903   77  255   25   60  11   3   1   25.0    ...      
85     abbotfr01    1904   41  130   14   22   4   2   0   12.0    ...      
98     abbotje01    1997   19   38    8   10   1   0   1    2.0    ...      
99     abbotje01    1998   89  244   33   68  14   1  12   41.0    ...      
113    abbotku01    1993   20   61   11   15   1   0   3    9.0    ...      
114    abbotku01    1994  101  345   41   86  17   3   9   33.0    ...      
126    abbotod01    1910   22   70    2   13   2   1   0    6.0    ...      
144    abercda01    1871    1    4    0    0   0   0   0    0.0    ...      
145    abercre01    2006  111  255   39   54  12   2   5   24.0    ...      
146    abercre01    2007   35   76   16   15   3   0   2    5.0    ...      
149    abernbr01    2001   79  304   43   82  17   1   5   33.0    ...      
150    abernbr01    2002  117  463   46  112  18   4   2   40.0    ...      
172    aberscl01    1947   47  140   24   39   6   3   4   20.0    ...      
173    aberscl01    1948   12   32    1    6   1   0   1    6.0    ...      
178    abnersh01    1987   16   47    5   13   3   1   2    7.0    ...      
179    abnersh01    1988   37   83    6   15   3   0   2    5.0    ...      
184    abramca01    1949    8   24    6    2   1   0   0    0.0    ...      
185    abramca01    1950   38   44    5    9   1   0   0    4.0    ...      
194    abreubo01    1996   15   22    1    5   1   0   0    1.0    ...      
...          ...     ...  ...  ...  ...  ...  ..  ..  ..    ...    ...      
96477   zinnfr01    1888    2    7    0    0   0   0   0    0.0    ...      
96478   zinngu01    1911    9   27    5    4   0   2   0    1.0    ...      
96479   zinngu01    1912  106  401   56  105  15  10   6   55.0    ...      
96489  zinteal01    2002   39   44    5    6   2   0   2    3.0    ...      
96490  zinteal01    2004   28   34    2    7   2   0   1    6.0    ...      
96491  zipfebu01    1961   50  170   17   34   7   5   4   18.0    ...      
96492  zipfebu01    1962   68  184   21   44   4   1   6   21.0    ...      
96493   ziskri01    1971    7   15    2    3   1   0   1    2.0    ...      
96494   ziskri01    1972   17   37    4    7   3   0   0    4.0    ...      
96521  zitzmbi01    1919   13   27    5    5   1   0   0    2.0    ...      
96522  zitzmbi01    1925  104  301   53   76  13   3   0   21.0    ...      
96529  zobribe01    2006   52  183   10   41   6   2   2   18.0    ...      
96530  zobribe01    2007   31   97    8   15   2   0   1    9.0    ...      
96541  zoccope01    2003   20   37    0    4   1   0   0    3.0    ...      
96551  zoskyed01    1991   18   27    2    4   1   1   0    2.0    ...      
96552  zoskyed01    1992    8    7    1    2   0   1   0    1.0    ...      
96567  zuberjo01    1996   30   91    7   23   4   0   1   10.0    ...      
96568  zuberjo01    1998   38   45    6   11   3   1   2    6.0    ...      
96569  zuletju01    2000   30   68   13   20   8   0   3   12.0    ...      
96570  zuletju01    2001   49  106   11   23   3   0   6   24.0    ...      
9657

In [22]:
panel_dict = defaultdict(dict)
for i in range(7):
    year = 'year' + str(i + 1)
    panel_dict[year] = new_df.groupby('playerID').nth(i).T.to_dict('index')

In [23]:
panel_dict

defaultdict(dict,
            {'year1': {'2B': {'aaronha01': 27,
               'abbotku01': 17,
               'abreubo01': 10,
               'adairje01': 21,
               'adamsbo03': 13,
               'adamssp01': 12,
               'adcocjo01': 16,
               'ageeto01': 27,
               'ainsmed01': 1,
               'aldremi01': 18,
               'alfoned01': 13,
               'alicelu01': 10,
               'allenbe01': 27,
               'allendi01': 38,
               'allenet01': 26,
               'alleyge01': 3,
               'allisbo01': 18,
               'allisdo01': 10,
               'almonbi01': 18,
               'alomaro01': 24,
               'alomasa01': 1,
               'alomasa02': 26,
               'aloufe01': 9,
               'alouje01': 11,
               'alouma01': 7,
               'aloumo01': 28,
               'altmage01': 14,
               'altuvjo01': 10,
               'alvarpe01': 21,
               'alvisma01': 32,
               'a

In [24]:
panel = pd.Panel(panel_dict)

In [25]:
panel

<class 'pandas.core.panel.Panel'>
Dimensions: 7 (items) x 2349 (major_axis) x 20 (minor_axis)
Items axis: year1 to year7
Major_axis axis: aaronha01 to zobribe01
Minor_axis axis: 2B to yearID

In [26]:
pd.DataFrame(panel['year3'])

2B  3B   AB   BB  CS    G GIDP    H HBP  HR IBB    R  RBI  SB SF  \
aaronha01  34  14  609   37   4  153   21  200   2  26   6  106   92   2  7   
abbotku01  18   7  320   22   3  109    7   81   3   8   1   37   33   3  0   
abreubo01  35  11  546  109   9  152   13  183   3  20   8  118   93  27  4   
adairje01  21   3  382    9   3  109   17   87   2   6   2   34   30   3  5   
adamsbo03  20   3  262   25   0   87    5   78   1   1   0   33   21   6  0   
adamssp01  29   8  627   44  12  149    0  180   7   2   0   95   48  26  0   
adcocjo01  22   4  378   23   4  117   10  105   1  13   0   43   52   1  0   
ageeto01   12   3  368   15   8  132    8   80   4   5   3   30   17  13  1   
ainsmed01   7   2  186   14   0   61    0   42   0   0   0   22   22   4  0   
aldremi01  15   0  389   56   5  139   10  104   0   3  13   44   50   6  3   
alfoned01  27   2  518   63   6  151    4  163   5  10   0   84   72  11  5   
alicelu01  19   3  362   47   1  115    9  101   4   3   2   50   46  11  7   
allenbe01   8   1  243   33   2   74    5   52   1   6   7   28   20   1  1   
allendi01  25  10  524   68   6  141    9  166   3  40  13  112  110  10  4   
allenet01  27  11  538   20   0  143    0  157   0   6   0   69   64  21  0   
alleyge01  28  10  579   27   8  147    8  173   5   7   0   88   43   8  3   
allisbo01  21   3  556  103   7  159   17  136   5  29   1   83  105   2  8   
allisdo01   6   0  128    3   0   30    2   34   0   0   0   17   11   0  0   
almonbi01   3   0  198   21   5  100    1   45   0   1   7   20    8   6  2   
alomaro01  27   5  586   48   7  147   16  168   2   6   1   80   60  24  5   
alomasa01  12   2  617   40   3  156    5  153   0   1   2   68   34  20  0   
alomasa02  16   0  299   13   3   89    7   75   5   2   3   22   26   3  0   
aloufe01   17   3  322   16   2  106    9   85   2   8   1   48   44  10  4   
alouje01   13   1  370    9   5  110   14   96   2   1   1   41   20   5  2   
alouma01    4   2  250   11   3  110    3   66   3   1   3   28   14   5  1   
aloumo01   31   5  422   42   6  107    7  143   2  22  10   81   78   7  5   
altmage01  28  12  518   40   2  138    4  157   4  27   3   77   96   6  7   
altuvjo01  31   2  626   32  13  152   24  177   2   5   5   64   52  35  8   
alvarpe01  25   1  525   57   0  149   10  128   1  30   6   64   85   1  3   
alvisma01  24   2  604   47   8  159    9  149   9  21   4   88   61  12  5   
...        ..  ..  ...  ...  ..  ...  ...  ...  ..  ..  ..  ...  ...  .. ..   
wynnji01   30   7  564   84   4  157   12  155   5  22   3   90   73  43  5   
wyrosjo01  24   9  512   52   0  136    5  140   3  17   0   74   76   7  0   
yastrca01  40   3  570   95   5  151   12  183   1  14   6   91   68   8  1   
yeagejo01   6   5  161    5   0   50    0   39   4   1   0   17   23   0  0   
yeagest01  16   1  316   32   2   94    7   84   2  12   5   41   41   2  3   
yorkru01   16   1  329   41   0  102    8  101   2  20   0   66   68   5  0   
yorkto01   11   7  278    3   1   57    0   84   0   2   0   70   50   4  0   
yosted01   19   7  435   91   3  124   11  110   1   9   0   57   45   3  0   
youklke01  35   2  528   77   2  145    9  152  15  16   0   85   83   4  5   
youngch04  28   4  433   59   4  134    3   92   4  15   2   54   42  11  2   
youngde03  28   4  575   35   5  152   19  167   7  10   7   80   69  14  5   
youngdm01  30   2  373   30   1  127   11  112   2  14   1   63   56   3  4   
younger01  13   1  228   38   7   90    3   62   2   7   1   37   30  18  2   
youngjo02  37   5  590   60  13  158    7  162   7  16   7   90   60  18  4   
youngke01   9   0  181    8   3   56    5   42   2   6   0   13   22   1  3   
youngmi02  33   9  666   36   2  160   14  204   1  14   1  106   72  13  7   
youngra01  18   2  503   61   0  141    0  116   3   1   0   64   35   8  0   
youngro01  27  14  581   75  18  153    0  204   2   6   0   92   78  18  0   
yountro01  19   3  638   38  11  161   13  161   0   2   3   

In [27]:
trimmed_df = dc.trim_batters(bat_with_pos_df)
trimmed_df['AVG'] = trimmed_df['H'] / trimmed_df['AB']
trimmed_df.drop(['H', 'AB'], axis=1, inplace=True)
trimmed_df

playerID  yearID    G    R  2B  3B  HR    RBI    SB    CS   BB     SO  \
9      aaronha01    1954  122   58  27   6  13   69.0   2.0   2.0   28   39.0   
10     aaronha01    1955  153  105  37   9  27  106.0   3.0   1.0   49   61.0   
11     aaronha01    1956  153  106  34  14  26   92.0   2.0   4.0   37   54.0   
12     aaronha01    1957  151  118  27   6  44  132.0   1.0   1.0   57   58.0   
13     aaronha01    1958  153  109  34   4  30   95.0   4.0   1.0   59   49.0   
14     aaronha01    1959  154  116  46   7  39  123.0   8.0   0.0   51   54.0   
15     aaronha01    1960  153  102  20  11  40  126.0  16.0   7.0   60   63.0   
114    abbotku01    1994  101   41  17   3   9   33.0   3.0   0.0   16   98.0   
115    abbotku01    1995  120   60  18   7  17   60.0   4.0   3.0   36  110.0   
116    abbotku01    1996  109   37  18   7   8   33.0   3.0   3.0   22   99.0   
117    abbotku01    1997   94   35  18   2   6   30.0   3.0   1.0   14   68.0   
118    abbotku01    1998   77   26  13   1   5   24.0   2.0   1.0   12   53.0   
119    abbotku01    1999   96   41  17   2   8   41.0   3.0   2.0   16   69.0   
120    abbotku01    2000   79   22   7   1   6   12.0   1.0   1.0   14   51.0   
195    abreubo01    1997   59   22  10   2   3   26.0   7.0   2.0   21   48.0   
196    abreubo01    1998  151   68  29   6  17   74.0  19.0  10.0   84  133.0   
197    abreubo01    1999  152  118  35  11  20   93.0  27.0   9.0  109  113.0   
198    abreubo01    2000  154  103  42  10  25   79.0  28.0   8.0  100  116.0   
199    abreubo01    2001  162  118  48   4  31  110.0  36.0  14.0  106  137.0   
200    abreubo01    2002  157  102  50   6  20   85.0  31.0  12.0  104  117.0   
201    abreubo01    2003  158   99  35   1  20  101.0  22.0   9.0  109  126.0   
311    adairje01    1961  133   41  21   1   9   37.0   5.0   2.0   35   51.0   
312    adairje01    1962  139   67  29   4  11   48.0   7.0   7.0   27   77.0   
313    adairje01    1963  109   34  21   3   6   30.0   3.0   3.0    9   51.0   
314    adairje01    1964  155   56  20   3   9   47.0   3.0   2.0   28   72.0   
315    adairje01    1965  157   51  26   3   7   66.0   6.0   4.0   35   65.0   
316    adairje01    1966  122   30  19   2   4   39.0   3.0   2.0   21   52.0   
317    adairje01    1967  117   47  17   1   3   35.0   1.0   5.0   17   52.0   
366    adamsbo03    1946   94   35  13   3   4   24.0  16.0   0.0   18   32.0   
367    adamsbo03    1947   81   39  11   2   4   20.0   9.0   0.0   25   23.0   
...          ...     ...  ...  ...  ..  ..  ..    ...   ...   ...  ...    ...   
96420  zimmedo01    1961  128   57  25   4  13   40.0   5.0   1.0   25   70.0   
96421  zimmedo01    1962   77   19  12   2   2   17.0   1.0   3.0   17   40.0   
96428  zimmehe01    1908   46   17   4   1   0    9.0   2.0   0.0    1    0.0   
96429  zimmehe01    1909   65   23   9   2   0   21.0   7.0   0.0    3    0.0   
96430  zimmehe01    1910   99   35  16   6   3   38.0   7.0   0.0   20   36.0   
96431  zimmehe01    1911  143   80  22  17   9   85.0  23.0   0.0   25   50.0   
96432  zimmehe01    1912  145   95  41  14  14   99.0  23.0   0.0   38   60.0   
96433  zimmehe01    1913  127   69  28  12   9   95.0  18.0   0.0   41   40.0   
96434  zimmehe01    1914  146   75  36  12   4   87.0  17.0   0.0   20   46.0   
96463  zimmery01    2006  157   84  47   3  20  110.0  11.0   8.0   61  120.0   
96464  zimmery01    2007  162   99  43   5  24   91.0   4.0   1.0   61  125.0   
96465  zimmery01    2008  106   51  24   1  14   51.0   1.0   1.0   31   71.0   
96466  zimmery01    2009  157  110  37   3  33  106.0   2.0   0.0   72  119.0   
96467  zimmery01    2010  142   85  32   0  25   85.0   4.0   1.0   69   98.0   
96468  zimmery01    2011  101   52  21   2  12   49.0   3.0   1.0   41   73.0   
96469  zimmery01    2012  145   93  36   1  25   95.0   5.0   2.0   57  116.0   
96495   ziskri01    1973  103   44  23   7  10   54.0   0.0   0.0   21   63.0   
96496   ziskri01    1974  149   75  30 

In [28]:
condensed_df = dc.condense_df(trimmed_df)
condensed_df.set_index('playerID', drop=True, inplace=True)
condensed_df

year1_2B  year1_3B  year1_AVG  year1_BB  year1_CS  year1_G  \
playerID                                                                
aaronha01        27         6   0.279915        28       2.0      122   
abbotku01        17         3   0.249275        16       0.0      101   
abreubo01        10         2   0.250000        21       2.0       59   
adairje01        21         1   0.264249        35       2.0      133   
adamsbo03        13         3   0.244373        18       0.0       94   
adamssp01        12         0   0.289389        26      19.0       95   
adcocjo01        16         1   0.293011        24       0.0      102   
ageeto01         27         8   0.273450        41      18.0      160   
ainsmed01         1         2   0.192308         6       0.0       33   
aldremi01        18         3   0.250000        33       3.0       84   
alfoned01        13         5   0.277612        12       1.0      101   
alicelu01        10         4   0.212121        25       1.0       93   
allenbe01        27         7   0.268761        62       1.0      159   
allendi01        38        13   0.318038        67       4.0      162   
allenet01        26         4   0.295265        14       0.0      111   
alleyge01         3         1   0.210526        21       1.0       81   
allisbo01        18         9   0.261404        60       8.0      150   
allisdo01        10         2   0.330827         0       1.0       27   
almonbi01        18        11   0.261011        37       9.0      155   
alomaro01        24         6   0.266055        47       6.0      143   
alomasa01         1         1   0.240741         4       5.0       67   
alomasa02        26         2   0.289888        25       1.0      132   
aloufe01          9         2   0.252747        19       2.0       75   
alouje01         11         0   0.273936        13       6.0      115   
alouma01          7         2   0.310000        15       2.0       81   
aloumo01         28         2   0.281525        25       2.0      115   
altmage01        14         4   0.245238        34       0.0      135   
altuvjo01        10         1   0.276018         5       3.0       57   
alvarpe01        21         1   0.256484        37       0.0       95   
alvisma01        32         7   0.274086        36       7.0      158   
...             ...       ...        ...       ...       ...      ...   
wynnji01         10         5   0.244000        30       2.0       70   
wyrosjo01        30         4   0.280734        70       0.0      145   
yastrca01        31         6   0.265866        50       5.0      148   
yeagejo01         5         1   0.171642         7       0.0       43   
yeagest01         0         1   0.273585        16       0.0       35   
yorkru01         18         3   0.306667        41       2.0      104   
yorkto01          5         7   0.255172         9       2.0       29   
yosted01         17         3   0.238318        45       5.0      115   
youklke01        11         0   0.259615        33       1.0       72   
youngch04        29         3   0.237258        43       6.0      148   
youngde03         9         1   0.317460         1       2.0       30   
youngdm01        14         3   0.258258        38       5.0      110   
younger01         1         0   0.257576         8       1.0       49   
youngjo02        13         1   0.244019        16       5.0       95   
youngke01        24         3   0.236080        36       2.0      141   
youngmi02        18         4   0.248705        26       1.0      106   
youngra01         6         5   0.243386        53      11.0      123   
youngro01        16         8   0.301688        44       0.0      121   
yountro01        14         5   0.250000        12       7.0      107   
zarilal01         7         1   0.254386        17       1.0       70   
zaungr01          5         0   0.259615        16       1.0       40   
zeidero01         9         2   0.216867        62       0.0      136

In [29]:
X_all = condensed_df
y_all = X_all.pop('year7_AVG')

In [30]:
X_train_all, X_test_all, y_train_all, y_true_all = train_test_split(X_all, y_all, test_size=0.2)

In [31]:
regr_all = RandomForestRegressor()
regr_all.fit(X_train_all, y_train_all)
y_all_pred = regr_all.predict(X_test_all)

In [32]:
results_all = pd.DataFrame(data=y_true_all)
results_all['predicted'] = y_all_pred
results_all['difference'] = results_all['year7_AVG'] - results_all['predicted']
results_all.reset_index(drop=True, inplace=True)
results_all

year7_AVG  predicted  difference
0     0.256489   0.256659   -0.000170
1     0.265690   0.265617    0.000073
2     0.235690   0.235820   -0.000130
3     0.209003   0.208880    0.000123
4     0.278592   0.278665   -0.000073
5     0.230769   0.230749    0.000020
6     0.291139   0.291077    0.000062
7     0.254658   0.254617    0.000041
8     0.285000   0.285024   -0.000024
9     0.214470   0.214529   -0.000058
10    0.159420   0.159639   -0.000219
11    0.266436   0.266575   -0.000139
12    0.294939   0.294856    0.000083
13    0.308197   0.308319   -0.000122
14    0.247458   0.247479   -0.000021
15    0.238298   0.238262    0.000036
16    0.284710   0.284717   -0.000007
17    0.310945   0.311088   -0.000143
18    0.272265   0.272153    0.000111
19    0.212560   0.212289    0.000272
20    0.311037   0.311342   -0.000306
21    0.280269   0.280196    0.000073
22    0.245495   0.245417    0.000079
23    0.302663   0.302737   -0.000074
24    0.147826   0.150052   -0.002226
25    0.282123   0.282222   -0.000099
26    0.250471   0.250326    0.000145
27    0.236686   0.237115   -0.000429
28    0.211538   0.211878   -0.000340
29    0.208955   0.208962   -0.000007
..         ...        ...         ...
440   0.309603   0.309645   -0.000042
441   0.283654   0.283578    0.000075
442   0.294545   0.294445    0.000101
443   0.324903   0.324859    0.000043
444   0.266272   0.266503   -0.000231
445   0.270925   0.270940   -0.000015
446   0.229965   0.229806    0.000159
447   0.272349   0.272153    0.000196
448   0.230277   0.230759   -0.000482
449   0.235507   0.235627   -0.000119
450   0.265979   0.266048   -0.000069
451   0.241379   0.241244    0.000136
452   0.260714   0.260710    0.000005
453   0.223350   0.223489   -0.000139
454   0.296099   0.296119   -0.000020
455   0.301266   0.301383   -0.000117
456   0.233422   0.233355    0.000066
457   0.259594   0.259814   -0.000220
458   0.248848   0.248909   -0.000061
459   0.230189   0.230528   -0.000339
460   0.252971   0.253081   -0.000110
461   0.317680   0.318419   -0.000739
462   0.219512   0.219413    0.000099
463   0.219355   0.219147    0.000208
464   0.210900   0.210802    0.000098
465   0.224852   0.224730    0.000122
466   0.261712   0.261705    0.000007
467   0.257683   0.257622    0.000061
468   0.192982   0.193800   -0.000817
469   0.244444   0.244534   -0.000090

[470 rows x 3 columns]

In [34]:
def get_metrics(X_test, y_true, y_pred, model):
    mse = mean_squared_error(y_true, y_pred)
    rmse = mse ** 0.5
    score = model.score(X_test, y_true)
    print('MSE:\t{:0.3f}\n'\
          'RMSE:\t{:0.3f}\n'\
          'Score:\t{:0.3f}'.format(mse, rmse, score))